In [1]:
!pip install osmnx==1.3.0

Defaulting to user installation because normal site-packages is not writeable


In [2]:
!pip install folium

Defaulting to user installation because normal site-packages is not writeable


In [3]:
!pip install osmnx geopandas

Defaulting to user installation because normal site-packages is not writeable


In [4]:
import osmnx as ox
import osmnx.folium as ox_folium
import pandas as pd
import geopandas as gpd
import folium
import numpy as np
import networkx as nx
import random
from collections import deque
from shapely.geometry import Point, LineString
import matplotlib.colors as mcolors

In [5]:
place_name = "City of Westminster"

# networkx graph
graph = ox.graph_from_address(place_name, dist=1000)

# Plot the graph using folium
m = ox_folium.plot_graph_folium(graph)
m 

In [6]:
# CSV containing LSOA and MSOA codes
codes_df = pd.read_csv('Data/Code Lookup.csv', encoding="latin1", low_memory=False)
# Open file for mean and stdev
with open('Mean_stdev.txt') as file:
    data = file.read()
    data_into_list = data.split("\n")
print(data_into_list)

['', '', 'Streaming output truncated to the last 5000 lines.', 'LSOA Barnet 027E: Mean = 2.8333333333333335, Stdev = 1.0671873729054748', 'LSOA Barnet 027F: Mean = 2.0952380952380953, Stdev = 1.341809790819559', 'LSOA Barnet 028A: Mean = 1.6, Stdev = 1.2000000000000002', 'LSOA Barnet 028B: Mean = 2.7142857142857144, Stdev = 1.3324827218698307', 'LSOA Barnet 028C: Mean = 2.4, Stdev = 1.4966629547095764', 'LSOA Barnet 028D: Mean = 2.642857142857143, Stdev = 1.493181782883348', 'LSOA Barnet 028E: Mean = 2.5, Stdev = 1.3601470508735443', 'LSOA Barnet 029A: Mean = 2.3, Stdev = 1.1', 'LSOA Barnet 029B: Mean = 2.5, Stdev = 1.3437096247164249', 'LSOA Barnet 029C: Mean = 2.2941176470588234, Stdev = 1.3618631650341442', 'LSOA Barnet 029D: Mean = 2.727272727272727, Stdev = 1.3876670474976134', 'LSOA Barnet 029E: Mean = 2.0, Stdev = 1.4675987714106855', 'LSOA Barnet 029F: Mean = 2.272727272727273, Stdev = 1.3876670474976134', 'LSOA Barnet 030A: Mean = 2.0, Stdev = 1.3165611772087666', 'LSOA Barnet

In [7]:
# Get all LSOA codes given MSOA name
msoa_name = "Westminster 018"
westminster_018_lsoas = codes_df[codes_df["msoa21nm"] == msoa_name]["lsoa21cd"].unique()

In [8]:
# Load the huge GeoJSON once (may take a while)
lsoa_gdf = gpd.read_file("Data/LSOA Boundaries 2021.geojson")

# Save it as a much faster binary format
lsoa_gdf.to_file("lsoas.gpkg", driver="GPKG")

DataSourceError: Data/LSOA Boundaries 2021.geojson: No such file or directory

In [185]:
# Filter for one LSOA
lsoa_code = "E01004763"
target_lsoa = lsoa_gdf[lsoa_gdf["LSOA21CD"] == lsoa_code]

# Ensure it's not empty
assert not target_lsoa.empty, "LSOA code not found."

# Extract and simplify the polygon
polygon = target_lsoa.geometry.values[0]
if polygon.geom_type == "MultiPolygon":
    polygon = max(polygon.geoms, key=lambda a: a.area)
polygon = polygon.simplify(0.001)

# Get the street network within the LSOA boundary
G = ox.graph_from_polygon(polygon, network_type="drive", simplify=True)

# Plot with folium
m = ox_folium.plot_graph_folium(G)
m

In [186]:
# Area map (not street view)
# Filter to only have the LSOAs in Westminster 018
subset = lsoa_gdf[lsoa_gdf["LSOA21CD"].isin(westminster_018_lsoas)]

# Get centroid to center the map
center = subset.unary_union.centroid.coords[:][0][::-1]  # (lat, lon)

# Create the folium map
m = folium.Map(location=center, zoom_start=15, tiles="cartodbpositron")

# Add the LSOA polygons
folium.GeoJson(
    subset,
    name="Westminster 018 LSOAs",
    style_function=lambda x: {
        "fillColor": "#3186cc",
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.4,
    },
    tooltip=folium.features.GeoJsonTooltip(fields=["LSOA21CD", "LSOA21NM"]),
).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

m

C:\Users\20221219\AppData\Local\Temp\ipykernel_9296\7478970.py:6: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  center = subset.unary_union.centroid.coords[:][0][::-1]  # (lat, lon)


In [187]:
# Combine all LSOA geometries into one polygon
combined_polygon = subset.unary_union

# Simplify the geometry
simplified_polygon = combined_polygon.simplify(0.001)

# Step 2: Get the street network within that area
G = ox.graph_from_polygon(simplified_polygon, network_type="drive")

# Step 3: Convert graph to a folium map
map = ox.folium.plot_graph_folium(G, tiles="cartodbpositron")

# Optional: add LSOA boundary overlay
folium.GeoJson(
    subset,
    name="Westminster 018 LSOAs",
    style_function=lambda x: {
        "fillColor": "none",
        "color": "blue",
        "weight": 2,
    },
).add_to(map)

# Optional: Add layer control
folium.LayerControl().add_to(map)

# Step 4: Display map
map


C:\Users\20221219\AppData\Local\Temp\ipykernel_9296\812482050.py:2: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  combined_polygon = subset.unary_union


In [188]:
# This is to turn G into undirected graph
# G = G.to_undirected(reciprocal = False)

In [189]:
# save the nodes and edges into variables
nodes, edges = ox.graph_to_gdfs(G, nodes=True, edges=True)

In [190]:
edges["weight"] = 0

In [191]:
# Reset the index so 'osmid' becomes a column
edges = edges.reset_index()

# Confirm we now have u, v, key
required_columns = ['u', 'v', 'key']
if all(col in edges.columns for col in required_columns):
    edges = edges.set_index(required_columns)
else:
    raise ValueError(f"Missing one of the required columns: {required_columns}")

In [192]:
# Sample 20 random edges
sampled_edges = edges.sample(n=20, random_state=42)

# Generate random weights between 1 and 10
random_weights = np.random.randint(1, 11, size=20)

# Assign the weights directly to the GeoDataFrame
edges.loc[sampled_edges.index, "weight"] = random_weights

In [193]:
for index, row in edges.iterrows():
    edges.at[index, 'hot'] = 1 if row['weight'] > 5 else 0

In [194]:
# Sort the edges GeoDataFrame by 'weight' column in descending order
edges_sorted = edges.sort_values(by="weight", ascending=False)

# Display the top 10 edges with the highest weights
print(edges_sorted[['osmid', 'weight']].head(30))

                                                                  osmid  \
u          v          key                                                 
25257815   25257813   0                                       237702242   
25257808   25257797   0                                         4253388   
9512922    26559655   0                                         4356104   
109836     9526047354 0                            [237462804, 2424941]   
25257324   109631     0               [1067635384, 1067635385, 4370943]   
361242661  25257815   0                                        86485148   
107816     9789818    0                                        53876143   
2390008569 1139318714 0                                         4256545   
1106056861 9515387    0                                      1136343319   
351771449  10574746   0                                        31476268   
9966771331 25257306   0                                       174326447   
256794572  2390005223 0  

In [195]:
# Check whether all edges in H exist in the graph
H = set(edges[edges['hot'] == 1].index)
missing_edges = [edge for edge in H if not G.has_edge(*edge)]

print(f"Missing edges: {missing_edges}")

Missing edges: []


In [196]:
hot_edges = edges[edges['hot'] == 1]
print(hot_edges[['weight']].describe())
print(hot_edges[hot_edges['weight'] > 0].shape)

          weight
count  10.000000
mean    7.500000
std     1.433721
min     6.000000
25%     6.250000
50%     7.000000
75%     8.750000
max    10.000000
(10, 17)


In [197]:
def find_unique_hot_routes(G, edges, nodes, k=5, m=1000, M=5000, max_iterations=1000):
    """
    Find unique routes with distinct starting segments.
    The first edge used is "hot".
    Route must be a cycle
    Uses directed graph G
    
    Parameters:
    - G: Original NetworkX graph
    - edges: GeoDataFrame with edge data
    - nodes: GeoDataFrame with node data
    - k: max routes to find
    - m: min route length
    - M: max route length
    - max_iterations: max attempts
    
    Returns:
    - List of (route, total_weight) tuples
    - working_G: The working graph
    """
    
    # Create working graph
    working_G = nx.DiGraph()
    for (u, v, key), row in edges.iterrows():
        length = row.get('length', 0)
        weight = row.get('weight', length)
        hot = row.get('hot', 0)
        
        working_G.add_edge(u, v, length=length, weight=weight, hot=hot, key=key)
        working_G.add_edge(v, u, length=length, weight=weight, hot=hot, key=key)
    
    routes_with_weights = []
    used_start_edges = set()
    iterations = 0
    
    # Get all hot edges once
    all_hot_edges = [
        (u, v) for u, v, data in working_G.edges(data=True)
        if data.get('hot', 0) == 1
    ]
    
    while (len(routes_with_weights) < k and 
           iterations < max_iterations and
           len(used_start_edges) < len(all_hot_edges)):
        
        iterations += 1
        
        # Get unused hot edges
        available_hot_edges = [
            edge for edge in all_hot_edges
            if edge not in used_start_edges
        ]
        
        if not available_hot_edges:
            break
            
        # Randomly select an unused starting edge
        # In next algorithm, can use hot edge with greatest weight as first edge of route
        start_edge = random.choice(available_hot_edges)
        start_node, next_node = start_edge
        
        # Initialize route tracking
        current_route = [start_node, next_node]
        current_length = working_G.edges[start_node, next_node]['length']
        current_weight = working_G.edges[start_node, next_node]['weight']
        visited_edges = {start_edge}
        
        # DFS stack: (node, route, length, weight, visited_edges)
        stack = deque([(next_node, current_route, current_length, current_weight, visited_edges)])
        
        found_route = None
        found_weight = 0
        
        while stack and not found_route:
            node, route, length, weight, visited = stack.pop()
            
            # Check if we can return to start
            if working_G.has_edge(node, start_node):
                return_edge = (node, start_node)
                if return_edge not in visited:
                    total_length = length + working_G.edges[node, start_node]['length']
                    total_weight = weight + working_G.edges[node, start_node]['weight']
                    if m <= total_length <= M:
                        found_route = route + [start_node]
                        found_weight = total_weight
                        break
            
            # Skip if over max length
            if length > M:
                continue
                
            # Explore neighbors
            for neighbor in working_G.neighbors(node):
                edge = (node, neighbor)
                if edge not in visited:
                    edge_data = working_G.edges[node, neighbor]
                    new_length = length + edge_data['length']
                    new_weight = weight + edge_data['weight']
                    
                    if new_length <= M:
                        new_visited = visited.copy()
                        new_visited.add(edge)
                        stack.append((neighbor, route + [neighbor], new_length, new_weight, new_visited))
        
        if found_route:
            # Check for duplicate routes
            is_duplicate = any(
                route == found_route 
                for route, _ in routes_with_weights
            )
            
            if not is_duplicate:
                routes_with_weights.append((found_route, found_weight))
                used_start_edges.add(start_edge)
    
    return routes_with_weights, working_G

In [198]:
def find_unique_hot_routes_ordered(G, edges, nodes, k=5, m=1000, M=5000, max_iterations=1000):
    """
    Find unique routes with distinct starting segments.
    The first edge used is "hot".
    Route must be a cycle
    Uses directed graph G
    
    Parameters:
    - G: Original NetworkX graph
    - edges: GeoDataFrame with edge data
    - nodes: GeoDataFrame with node data
    - k: max routes to find
    - m: min route length
    - M: max route length
    - max_iterations: max attempts
    
    Returns:
    - List of (route, total_weight) tuples
    - working_G: The working graph
    """
    
    # Create working graph
    working_G = nx.DiGraph()
    for (u, v, key), row in edges.iterrows():
        length = row.get('length', 0)
        weight = row.get('weight', length)
        hot = row.get('hot', 0)
        
        working_G.add_edge(u, v, length=length, weight=weight, hot=hot, key=key)
        working_G.add_edge(v, u, length=length, weight=weight, hot=hot, key=key)
    
    routes_with_weights = []
    used_start_edges = set()
    iterations = 0
    
    # Get all hot edges once
    all_hot_edges = [
        (u, v) for u, v, data in working_G.edges(data=True)
        if data.get('hot', 0) == 1
    ]
    
    while (len(routes_with_weights) < k and 
           iterations < max_iterations and
           len(used_start_edges) < len(all_hot_edges)):
        
        iterations += 1
        
        # Get unused hot edges
        available_hot_edges = [
            edge for edge in all_hot_edges
            if edge not in used_start_edges
        ]
        
        if not available_hot_edges:
            break
            
        # Select available_hot_edge with maximum weight
        start_edge = max(
            available_hot_edges,
            key = lambda edge: working_G.edges[edge]['weight']
        )
        start_edge_reversed = (start_edge[1], start_edge[0])
        start_node, next_node = start_edge
        
        # Initialize route tracking
        current_route = [start_node, next_node]
        current_length = working_G.edges[start_node, next_node]['length']
        current_weight = working_G.edges[start_node, next_node]['weight']
        visited_edges = {start_edge}
        
        # DFS stack: (node, route, length, weight, visited_edges)
        stack = deque([(next_node, current_route, current_length, current_weight, visited_edges)])
        
        found_route = None
        found_weight = 0
        
        while stack and not found_route:
            node, route, length, weight, visited = stack.pop()
            
            # Check if we can return to start
            if working_G.has_edge(node, start_node):
                return_edge = (node, start_node)
                if return_edge not in visited:
                    total_length = length + working_G.edges[node, start_node]['length']
                    total_weight = weight + working_G.edges[node, start_node]['weight']
                    
                    if m <= total_length <= M:
                        found_route = route + [start_node]
                        found_weight = total_weight
                        break
            
            # Skip if over max length
            if length > M:
                continue
                
            # Explore neighbors
            for neighbor in working_G.neighbors(node):
                edge = (node, neighbor)
                if edge not in visited:
                    edge_data = working_G.edges[node, neighbor]
                    new_length = length + edge_data['length']
                    new_weight = weight + edge_data['weight']
                    
                    if new_length <= M:
                        new_visited = visited.copy()
                        new_visited.add(edge)
                        stack.append((neighbor, route + [neighbor], new_length, new_weight, new_visited))
        
        if found_route:
            # Check for duplicate routes
            is_duplicate = any(
                route == found_route 
                for route, _ in routes_with_weights
            )
            
            if not is_duplicate:
                routes_with_weights.append((found_route, found_weight))
                used_start_edges.add(start_edge)
                used_start_edges.add(start_edge_reversed)
    
    return routes_with_weights, working_G

In [199]:
def find_max_weight_routes(G, edges, nodes, k=5, m=1000, M=5000, max_iterations=1000):
    # Create working graph (same as before)
    working_G = nx.DiGraph()
    for (u, v, key), row in edges.iterrows():
        length = row.get('length', 0)
        weight = row.get('weight', length)
        working_G.add_edge(u, v, length=length, weight=weight, key=key)
        working_G.add_edge(v, u, length=length, weight=weight, key=key)
    
    routes_with_weights = []
    used_start_edges = set()
    
    # Get all edges sorted by weight (descending)
    all_edges = sorted(
        [(u, v) for u, v in working_G.edges()],
        key=lambda e: -working_G.edges[e]['weight']
    )
    
    for start_edge in all_edges:
        if len(routes_with_weights) >= k:
            break
            
        if start_edge in used_start_edges:
            continue
            
        start_node, next_node = start_edge
        best_route, best_weight = None, 0
        stack = deque([(
            next_node, 
            [start_node, next_node], 
            working_G.edges[start_edge]['length'],
            working_G.edges[start_edge]['weight'],
            {start_edge}
        )])
        
        while stack:
            node, route, length, weight, visited = stack.pop()
            
            # Check cycle completion
            if working_G.has_edge(node, start_node):
                return_edge = (node, start_node)
                if return_edge not in visited:
                    total_length = length + working_G.edges[return_edge]['length']
                    total_weight = weight + working_G.edges[return_edge]['weight']
                    
                    if m <= total_length <= M and total_weight > best_weight:
                        best_route = route + [start_node]
                        best_weight = total_weight
                        continue  # Keep looking for heavier cycles
            
            # Explore neighbors sorted by weight (descending)
            for neighbor in sorted(
                working_G.neighbors(node),
                key=lambda n: -working_G.edges[node, n]['weight']
            ):
                edge = (node, neighbor)
                if edge not in visited:
                    edge_data = working_G.edges[edge]
                    new_length = length + edge_data['length']
                    new_weight = weight + edge_data['weight']
                    
                    if new_length <= M:
                        new_visited = visited.copy()
                        new_visited.add(edge)
                        stack.append((neighbor, route + [neighbor], new_length, new_weight, new_visited))
        
        if best_route:
            # Check for duplicates
            if not any(r == best_route for r, _ in routes_with_weights):
                routes_with_weights.append((best_route, best_weight))
                used_start_edges.add(start_edge)
    
    return sorted(routes_with_weights, key=lambda x: -x[1]), working_G

In [200]:
def find_max_weight_routes_fast(G, edges, nodes, k=5, m=1000, M=5000, max_iterations=100, beam_width=3, neighbor_sample=5):
    # Create working graph
    working_G = nx.DiGraph()
    for (u, v, key), row in edges.iterrows():
        length = row.get('length', 0)
        weight = row.get('weight', length)
        working_G.add_edge(u, v, length=length, weight=weight, key=key)
        working_G.add_edge(v, u, length=length, weight=weight, key=key)
    
    routes_with_weights = []
    used_start_edges = set()
    
    # Pre-sort all edges by weight
    all_edges = sorted(
        [(u, v) for u, v in working_G.edges()],
        key=lambda e: -working_G.edges[e]['weight']
    )
    
    for start_edge in all_edges:
        if len(routes_with_weights) >= k:
            break
        if start_edge in used_start_edges:
            continue
            
        start_node, next_node = start_edge
        best_route, best_weight = None, 0
        initial_state = (
            next_node,
            [start_node, next_node],
            working_G.edges[start_edge]['length'],
            working_G.edges[start_edge]['weight'],
            {start_edge}
        )
        beam = [initial_state]
        
        while beam and len(routes_with_weights) < k:
            new_beam = []
            
            for state in beam:
                node, route, length, weight, visited = state
                
                # Check cycle completion
                if working_G.has_edge(node, start_node):
                    return_edge = (node, start_node)
                    if return_edge not in visited:
                        total_length = length + working_G.edges[return_edge]['length']
                        total_weight = weight + working_G.edges[return_edge]['weight']
                        
                        if m <= total_length <= M and total_weight > best_weight:
                            best_route = route + [start_node]
                            best_weight = total_weight
                
                # Skip if no hope of reaching min length
                min_possible_length = length + nx.shortest_path_length(working_G, node, start_node, weight='length')
                if min_possible_length > M:
                    continue
                
                # Get top-k heaviest neighbors
                neighbors = sorted(
                    working_G.neighbors(node),
                    key=lambda n: -working_G.edges[node, n]['weight']
                )[:neighbor_sample]
                
                for neighbor in neighbors:
                    edge = (node, neighbor)
                    if edge not in visited:
                        edge_data = working_G.edges[edge]
                        new_length = length + edge_data['length']
                        new_weight = weight + edge_data['weight']
                        
                        if new_length <= M:
                            new_visited = visited.copy()
                            new_visited.add(edge)
                            new_state = (neighbor, route + [neighbor], new_length, new_weight, new_visited)
                            new_beam.append(new_state)
            
            # Keep only top beam_width states by weight
            beam = sorted(new_beam, key=lambda x: -x[3])[:beam_width]
        
        if best_route and best_route not in [r for r, _ in routes_with_weights]:
            routes_with_weights.append((best_route, best_weight))
            used_start_edges.add(start_edge)
    
    return sorted(routes_with_weights, key=lambda x: -x[1]), working_G

In [201]:
def find_max_weight_routes_fast_2(G, edges, nodes, k=5, m=1000, M=5000, max_iterations=100, beam_width=3, neighbor_sample=5, max_overlap=5):
    # Create working graph
    working_G = nx.DiGraph()
    for (u, v, key), row in edges.iterrows():
        length = row.get('length', 0)
        weight = row.get('weight', length)
        working_G.add_edge(u, v, length=length, weight=weight, key=key)
        working_G.add_edge(v, u, length=length, weight=weight, key=key)
    
    routes_with_weights = []
    used_start_edges = set()
    all_used_edges = []  # List of sets containing used edges for each route
    
    # Pre-sort all edges by weight
    all_edges = sorted(
        [(u, v) for u, v in working_G.edges()],
        key=lambda e: -working_G.edges[e]['weight']
    )
    
    for start_edge in all_edges:
        if len(routes_with_weights) >= k:
            break
        if start_edge in used_start_edges:
            continue
            
        start_node, next_node = start_edge
        best_route, best_weight = None, 0
        initial_state = (
            next_node,
            [start_node, next_node],
            working_G.edges[start_edge]['length'],
            working_G.edges[start_edge]['weight'],
            {start_edge, (next_node, start_node)}  # Track both directions
        )
        beam = [initial_state]
        
        while beam and len(routes_with_weights) < k:
            new_beam = []
            
            for state in beam:
                node, route, length, weight, visited = state
                
                # Check cycle completion
                if working_G.has_edge(node, start_node):
                    return_edge = (node, start_node)
                    if return_edge not in visited:
                        total_length = length + working_G.edges[return_edge]['length']
                        total_weight = weight + working_G.edges[return_edge]['weight']
                        
                        if m <= total_length <= M and total_weight > best_weight:
                            candidate_route = route + [start_node]
                            candidate_edges = visited.union({return_edge, (start_node, node)})
                            
                            # Check overlap with existing routes
                            valid = True
                            for used_edges in all_used_edges:
                                overlap = len(candidate_edges.intersection(used_edges))
                                if overlap > max_overlap:
                                    valid = False
                                    break
                            
                            if valid:
                                best_route = candidate_route
                                best_weight = total_weight
                                best_edges = candidate_edges
                
                # Skip if no hope of reaching min length
                min_possible_length = length + nx.shortest_path_length(working_G, node, start_node, weight='length')
                if min_possible_length > M:
                    continue
                
                # Get top-k heaviest neighbors
                neighbors = sorted(
                    working_G.neighbors(node),
                    key=lambda n: -working_G.edges[node, n]['weight']
                )[:neighbor_sample]
                
                for neighbor in neighbors:
                    edge = (node, neighbor)
                    reverse_edge = (neighbor, node)
                    if edge not in visited and reverse_edge not in visited:
                        edge_data = working_G.edges[edge]
                        new_length = length + edge_data['length']
                        new_weight = weight + edge_data['weight']
                        
                        if new_length <= M:
                            new_visited = visited.copy()
                            new_visited.add(edge)
                            new_visited.add(reverse_edge)
                            new_state = (neighbor, route + [neighbor], new_length, new_weight, new_visited)
                            new_beam.append(new_state)
            
            # Keep only top beam_width states by weight
            beam = sorted(new_beam, key=lambda x: -x[3])[:beam_width]
        
        if best_route:
            routes_with_weights.append((best_route, best_weight))
            all_used_edges.append(best_edges)
            used_start_edges.add(start_edge)
            # Also add reverse direction to prevent starting from it
            used_start_edges.add((start_edge[1], start_edge[0]))
    
    return sorted(routes_with_weights, key=lambda x: -x[1]), working_G

In [208]:
print(max(
            working_G.edges,
            key = lambda edge: working_G.edges[edge]['weight']
        ))

(25257813, 25257815)


In [204]:
routes, working_G = find_max_weight_routes_fast_2(G, edges, nodes, k=5, m=800, M=3000, beam_width=50, neighbor_sample=50)
i = 0
for route, weight in routes:
    print(f"Route {i+1}:")
    print(f"  Start edge: {route[0]}→{route[1]}")
    print(f"  Nodes: {route}")
    print(f"  Weight: {weight:.2f}")
    print(f"  Length: {sum(working_G.edges[route[i], route[i+1]]['length'] for i in range(len(route)-1)):.2f}m")
    i = i + 1

Route 1:
  Start edge: 361242661→25257815
  Nodes: [361242661, 25257815, 25257813, 25257810, 25257793, 25257794, 1947328065, 25257795, 25257797, 25257808, 6250236322, 6250236321, 109579, 76465624, 25507240, 109577, 6250236319, 361242661]
  Weight: 26.00
  Length: 1191.00m
Route 2:
  Start edge: 25257813→25257815
  Nodes: [25257813, 25257815, 361242661, 361242424, 9966771331, 25257306, 1691133712, 454212847, 9966771334, 1691133703, 9966771320, 9966771331, 25257813]
  Weight: 22.00
  Length: 913.08m
Route 3:
  Start edge: 9512922→26559655
  Nodes: [9512922, 26559655, 6214704100, 26559582, 107801, 107799, 107798, 7889967240, 9789808, 107818, 25257616, 6266808742, 6266808745, 109631, 25257324, 108267, 108085, 11707733694, 11707733695, 2215490966, 9789816, 6914171275, 26591535, 26591530, 26591529, 9789809, 9789806, 9789817, 9789820, 9789818, 107816, 1598214606, 4580163090, 107802, 9398094483, 26573672, 26573667, 9512922]
  Weight: 20.00
  Length: 2482.50m
Route 4:
  Start edge: 9515387→1106

In [205]:
# Check if all nodes in your route exist in the graph
missing_nodes = [node for node in route if node not in G.nodes]
print(f"Missing nodes: {missing_nodes}")

Missing nodes: []


In [206]:
# Combine all LSOA geometries into one polygon
combined_polygon = subset.unary_union

# Simplify the geometry
simplified_polygon = combined_polygon.simplify(0.001)

# Get the street network within that area
G = ox.graph_from_polygon(simplified_polygon, network_type="drive")

# Convert graph to a folium map
map = ox.folium.plot_graph_folium(G, tiles="cartodbpositron")

# Optional: add LSOA boundary overlay
folium.GeoJson(
    subset,
    name="Westminster 018 LSOAs",
    style_function=lambda x: {
        "fillColor": "none",
        "color": "blue",
        "weight": 2,
    },
).add_to(map)

# Weird with loop for some reason?
i = 1
for route in routes:
    route_geoms = []
    for u, v in zip(route[0][:-1], route[0][1:]):
        if G.has_edge(u, v):
            data = G.edges[u, v, 0]
        elif G.has_edge(v, u):
            data = G.edges[v, u, 0]
        else:
            print(f"Missing edge between {u} and {v}")
            continue
            
        if 'geometry' in data:
            route_geoms.append(data['geometry'])
        else:
            # Create straight line if no geometry
            u_pt = Point(G.nodes[u]['x'], G.nodes[u]['y'])
            v_pt = Point(G.nodes[v]['x'], G.nodes[v]['y'])
            route_geoms.append(LineString([u_pt, v_pt]))
    
    if route_geoms:
        gdf_route = gpd.GeoDataFrame(geometry=route_geoms, crs="EPSG:4326")
        folium.GeoJson(
            gdf_route,
            name="Route " + str(i),
            style_function=lambda x: {
                "color": "red",
                "weight": 5,
                "opacity": 1,
            }
        ).add_to(map)
    i = i + 1
    
folium.LayerControl().add_to(map)

map

C:\Users\20221219\AppData\Local\Temp\ipykernel_9296\2288795352.py:2: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  combined_polygon = subset.unary_union


In [210]:
# map.save("Westminster Routes 20-05.html")